# nb-model_exp-results

In [1]:
import sys
import os
from os import sep
from os.path import dirname, realpath, exists, basename
from pathlib import Path
from glob import glob, iglob
import logging

def get_cwd(fname, subdir, crunch_dir=realpath(Path.home()) +sep +'crunch' +sep):
    """
    Convenience function to make a directory string for the current file based on inputs.
    Jupyter Notebook in Anaconda invokes the Python interpreter in Anaconda's subdirectory
    which is why changing sys.argv[0] is necessary. In the future a better way to do this
    should be preferred..
    """
    return crunch_dir +subdir +fname

def fix_path(cwd):
    """
    Convenience function to fix argv and python path so that jupyter notebook can run the same as
    any script in crunch.
    """
    sys.argv[0] = cwd
    module_path = os.path.abspath(os.path.join('..'))
    if module_path not in sys.path:
        sys.path.append(module_path)

fname = 'nb-model_exp-results.ipynb'
dir_name = 'model'
fix_path(get_cwd(fname, dir_name +sep))

import numpy as np
import pandas as pd

from ipywidgets import interact, interactive, fixed
from IPython.display import display

pd.set_option("display.max_rows", 300)
pd.set_option("display.max_columns", 50)

from common_util import MODEL_DIR, load_json, dump_json, rectify_json, load_df, str_now, makedir_if_not_exists, is_valid, isnt, compose, pd_split_ternary_to_binary, df_del_midx_level, midx_intersect, pd_get_midx_level, pd_rows, df_midx_restack
from common_util import NestedDefaultDict
from model.common import EXP_LOG_DIR, EXP_PARAMS_DIR, ASSETS, DATASET_DIR, XG_PROCESS_DIR, XG_DATA_DIR, XG_DIR, PYTORCH_MODELS_DIR, TRAIN_RATIO, EXPECTED_NUM_HOURS
from recon.viz import *
logging.basicConfig(stream=sys.stdout, level=logging.DEBUG)

CRITICAL:root:script location: /home/kev/crunch/model/nb-model_exp-results.ipynb
CRITICAL:root:using project dir: /home/kev/crunch/


Prune the xg data down to the data of interest to use in further experiments.

In [2]:
def get_bench(pattern):
    ndd = NestedDefaultDict()
    for path in iglob(pattern, recursive=True):
        ndd[path.split('/')] = load_json(path)

    df_idx = [k[2] for k in ndd.keys()]
    df = pd.DataFrame.from_records([b['benchmark-hold'] for b in ndd.values()], index=df_idx)

    return df

In [3]:
def consolidate_results(pattern, bench_pattern=None):
    ndd = NestedDefaultDict()
    for path in iglob(pattern, recursive=True):
        ndd[path.split('/')] = load_json(path)
    df_keys = [(k[2], k[3], k[4], k[5], k[6]) for k in ndd.keys()]
    df_idx = pd.MultiIndex.from_tuples(df_keys, names=('asset', 'model', 'data', 'params', 'trial')) \
        .remove_unused_levels()
    df = pd.DataFrame.from_records(list(ndd.values()), index=df_idx) \
        .reset_index() \
        .groupby(['asset', 'model', 'params']).mean() # average across trials for each study

    if (is_valid(bench_pattern)):
        bench_df = get_bench(bench_pattern)
        mets = ['accuracy', 'precision', 'recall', 'f1']
        rets = ['profit', 'sharpe', 'cagr']
        for m in mets+rets:
            res_cols = [c for c in df.columns if (c.endswith(m))]
            bench_cols = [c for c in bench_df.columns if (c.endswith(m))]
            bench_col = bench_cols[0]

            for asset in bench_df.index:
#                 print(bench_df.loc[asset, bench_col])
#                 print(df.xs(asset, level=0, drop_level=False)[res_cols])
                df.xs(asset, level=0, drop_level=False).loc[:, res_cols] -= bench_df.loc[asset, bench_col]
#     df = df.style \
#         .background_gradient(subset=[c for c in df.columns if c.endswith(('accuracy', 'profit', 'sharpe', 'cagr'))], cmap='BuGn')
#     .set_sticky(axis="index") \
    return df

In [4]:
def agg_asset(res_df):
    agg_df = res_df.groupby(['model', 'params']).mean()
    return agg_df

In [5]:
def agg_model(res_df):
    agg_df = res_df.groupby(['params']).mean()
    return agg_df

In [6]:
def add_style(df):
    df = df.style \
         .background_gradient(subset=[c for c in df.columns if c.endswith(('accuracy', 'f1', 'profit', 'sharpe', 'cagr'))], cmap='BuGn')
#     .set_sticky(axis="index") \
    return df

In [7]:
view = ('accuracy', 'f1', 'profit', 'sharpe', 'cagr')

def select_ends(df, ends=view):
    res_cols = [c for c in df.columns if (c.endswith(ends))]
#     for m in ends:
#         res_cols = [c for c in df.columns if (c.endswith(m))]
    return df.loc[:, res_cols]

In [8]:
def gb_filter_monotonic(df, checkcol='val_binary_sharpe'):
    return df.reorder_levels(['params', 'model']) \
            .groupby('params') \
            .apply(lambda g: g if (g[checkcol].is_monotonic_increasing) else None) \
            .sort_index()

def gb_filter_lf(df, checkcol='val_binary_longfreq'):
    return df.groupby('params') \
            .apply(lambda g: g if ((g[checkcol].between(.2, .8)).all()) else None)

In [9]:
# def get_params_per_dataset():
#     EXP_LOG_DIR

In [10]:
exp_base = basename(dirname(EXP_LOG_DIR))
sm_name = 'anp'
#drange = '2007_2018'
drange = '2009_2018'
#xdata = 'h_pba_h_h_vol_h'
xdata = 'h_pba_h'
ydata = 'ddir'
data_name = f'{drange}_{ydata}_{xdata}'
bench_data_name = f'{drange}_{ydata}'

path_train = f"{exp_base}/{sm_name}/**/{data_name}/**/train.json"
path_val =   f"{exp_base}/{sm_name}/**/{data_name}/**/val.json"
# path_test = f"{exp_base}/{sm_name}/**/{data_name}/**/test.json"

path_bench_train = f"{exp_base}/bench/*/{bench_data_name}/train.json"
path_bench_val = f"{exp_base}/bench/*/{bench_data_name}/val.json"
# path_bench_test = f"{exp_base}/bench/*/{bench_data_name}/test.json"

In [11]:
# absolute results
dt = consolidate_results(path_train);
dv = consolidate_results(path_val);

# benchmark adjusted results
dt_adj = consolidate_results(path_train, path_bench_train);
dv_adj = consolidate_results(path_val, path_bench_val);

/home/kev/miniconda3/lib/python3.8/site-packages/pandas/core/indexing.py:1787: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  self._setitem_single_column(loc, val, pi)


## Training Set Results

In [12]:
# 11 - 20: bn2d, in2d: best results so far
#X 21 - 30: (11-20) -> Disabled resampling: overfitting (long freq too high)
#X 31 - 40: (21-30) -> doubled batch size: overfitting, but less than 21-30
# 41 - 50: (11-20) -> doubled batch_size: a few good studies
# 51 - 60: (11-20) -> halved window_size: a few good studies
# *1 -> 14
# *2 -> 15
# *3 -> 16
# *4 -> 20
# *5 -> 44
# *6 -> 45
# *7 -> 54
# *8 -> 55
# *9 -> 56
# *0 -> 60

# 61 - 70: (14-16,20,44-45,54-56,60) -> use normal output dist: degraded performance
# 71 - 80: (14-16,20,44-45,54-56,60) -> sample_latent_post->true: degraded performance a little
# 81 - 90: (14-16,20,44-45,54-56,60) -> act_output->true: worse
# 91 - 100: (14-16,20,44-45,54-56,60) -> output xavier_uniform -> xavier_normal: one study better than all previous, but generally not decisive across the board
# 101 - 110: (14-16,20,44-45,54-56,60) -> output xavier_uniform -> kaiming_uniform: one study with best result so far
# 111 - 120: (14-16,20,44-45,54-56,60) -> output xavier_uniform -> kaiming_normal: mediocre

# XXX - revisit using kaiming_{uniform, normal} in the future, for now go back to xavier_uniform
# 121 - 130: (14-16,20,44-45,54-56,60) -> output FFN topology [128, 128]: 
# 131 - 140: (14-16,20,44-45,54-56,60) -> output dropout .2 to .4:

# 140 - 150: (14-16,20,44-45,54-56,60) -> quarter the window size:


In [13]:
AST = 'sp_500'

In [14]:
add_style(gb_filter_lf(gb_filter_monotonic(dv_adj.loc[AST])))

In [17]:
add_style(gb_filter_lf(gb_filter_monotonic(dv_adj.loc[AST])))

In [18]:
add_style(dv_adj.loc[AST].reorder_levels(['params', 'model']).sort_index())

In [19]:
add_style(agg_model(agg_asset(dt_adj)))

In [20]:
add_style(agg_model(agg_asset(dv_adj)))

In [21]:
for i in [34, 54, 60, 97, 101, 110, 120, 137]:
    display(show_res(str(i)))

NameError: name 'show_res' is not defined

## Compare Results Over Val by Params

In [23]:
show_tres = lambda p: add_style(select_ends(dt_adj.xs(p, level=2, drop_level=False)))
show_res = lambda p: add_style(select_ends(agg_asset(dv_adj.xs(p, level=2, drop_level=False))))
show_res1 = lambda p: add_style(select_ends(dv_adj.xs(p, level=2, drop_level=False)))
show_res2 = lambda p: add_style(select_ends(agg_model(agg_asset(dv_adj.xs(p, level=2, drop_level=False)))))

In [24]:
show_tres = lambda p: add_style(select_ends(dt.xs(p, level=2, drop_level=False)))
show_vres = lambda p: add_style(select_ends(dv.xs(p, level=2, drop_level=False)))
show_tres_adj = lambda p: add_style(select_ends(dt_adj.xs(p, level=2, drop_level=False)))
show_vres_adj = lambda p: add_style(select_ends(dv_adj.xs(p, level=2, drop_level=False)))

In [25]:
for i in [60, 97, 101, 110, 120, 127, 209]:
#     display(show_tres(str(i)))
    display(show_tres_adj(str(i)))
#     display(show_vres(str(i)))
    display(show_vres_adj(str(i)))

In [23]:
for i in [60]:
    display(show_tres(str(i)))
    display(show_res1(str(i)))
    display(show_res(str(i)))
    display(show_res2(str(i)))

In [107]:
# h_pba_hmz split feat norm (no input norm) for bn2d and in2d
for i in range(40, 50):
    display(show_res(str(i)))

In [108]:
# h_pba_mz split feat norm (no input norm) for bn2d and in2d
for i in range(17, 19):
    display(show_res(str(i)))

In [124]:
# h_pba_hmz (split, double unsplit, double split) for bn2d and in2d normalizers
for i in range(11,17):
    display(show_res(str(i)))

In [130]:
# h_pba_mz (split, double unsplit, double split) for bn2d and in2d normalizers
for i in range(11,17):
    display(show_res(str(i)))

In [114]:
# h_pba_hmz
for i in [2, 6]:
    display(show_res(str(i)))

In [108]:
# h_pba_mz
for i in [2, 6]:
    display(show_res(str(i)))

In [101]:
# h_pba_z
for i in [2, 6, 7]:
    display(show_res(str(i)))

In [93]:
#h_pba_m
for i in [2, 6, 7]:
    display(show_res(str(i)))

In [86]:
# h_pba_h
for i in [2, 6, 7]:
    display(show_res(str(i)))

In [87]:
for i in range(11):
    display(show_res(str(i)))